In [30]:
# conda install scikit-learn
# install from: http://docs.python-requests.org/en/master/
# to fix ssl installation of python packages issue
# curl https://bootstrap.pypa.io/get-pip.py | python3
# instructions to setup virtualenv
# https://www.tensorflow.org/install/install_mac
# pip3 install -r requirements.txt
# https://www.datacamp.com/community/tutorials/tensorflow-tutorial
# https://github.com/jtopor/CUNY-MSDA-661/blob/master/CIFAR-100/TF-Layers-CIFAR-100-v2.py

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import requests
import cv2
import h5py
import scipy.misc
import numpy as np
import csv
import sklearn.model_selection as model
import pickle 
import tensorflow as tf

from csv import DictReader
from urllib.request import urlopen
from matplotlib.pyplot import imshow
from fr_utils import *
from inception_blocks_v2 import *
from skimage import transform
from tensorflow.contrib import learn
from tensorflow.contrib.learn.python.learn.estimators import model_fn as model_fn_lib

%matplotlib inline
%load_ext autoreload
%autoreload

learning_rate = 0.001

np.set_printoptions(threshold=np.nan)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [31]:
def convert_input_format(data):    
    return np.transpose(
        np.reshape(data, (-1, 32, 32, 3), order="F"),
        axes=(0, 2, 1, 3)
    )

def convert_output_labels(data):
    return np.asarray(data['fine_labels'], dtype=np.int32)

def one_hot_labels(labels):
    return tf.one_hot(indices=tf.cast(labels, tf.int32), depth=100)

def unpickle(file):
    fo = open(file, "rb")
    dict = pickle.load(fo, encoding="latin1")
    fo.close()
    return dict

In [32]:
def conv_layer(input_layer, filters=32, kernel_size=[5,5]):
    # setting up the conv layer, with stride and padding
    return tf.layers.conv2d(
        inputs=input_layer,
        filters=filters,
        kernel_size=kernel_size,
        padding="same",
        activation=tf.nn.relu
    )

def maxpool_layer(conv, pool_size=[2,2], strides=2):
    return tf.layers.max_pooling2d(
        inputs=conv, pool_size=pool_size, strides=strides
    )

def dropout_layer(inputs, mode, rate=0.25):
    
    return tf.layers.dropout(
        inputs=inputs, rate=rate, training=mode == learn.ModeKeys.TRAIN
    )

def dense_layer(inputs, units, activation=tf.nn.relu):
    return tf.layers.dense(inputs=inputs, units=units, activation=activation)

def determine_loss(labels, logits, mode):
    print(mode)
#     if mode != learn.ModeKeys.INFER:
    return tf.losses.softmax_cross_entropy (
        onehot_labels=one_hot_labels(labels),
        logits=logits
    )
#     else:
#         return None
    
def determine_train_op(loss, mode):
    print(mode)
#     if mode == learn.ModeKeys.TRAIN:
    return tf.contrib.layers.optimize_loss (
        loss=loss, 
        global_step=tf.contrib.framework.get_global_step(),
        learning_rate=0.0001,
        optimizer="Adam"
    )
#     else:
#         return None
    
def generate_predictions(logits):
    return {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

def cnn_model(features, labels, mode): 
    mode = learn.ModeKeys.TRAIN if mode == "train" else learn.ModeKeys.INFER
    input_layer = tf.convert_to_tensor(features)
    
    # cnn layer 1
    conv1 = conv_layer(input_layer)
    conv2 = conv_layer(conv1)
    
    # pooling layer 1 
    pool1 = maxpool_layer(conv2)
    
    # dropout operation
    dropout1 = dropout_layer(pool1, mode)
    
    # cnn layer 2 
    conv3 = conv_layer(dropout1, 64, [3, 3])
    conv4 = conv_layer(conv3, 64, [3, 3])
    
    # pooling layer 2
    pool2 = maxpool_layer(conv4)
    
    # dropout operation
    dropout2 = dropout_layer(pool2, mode)
    
    # flatten tensor into a batch of vectors
    pool2_flat = tf.reshape(dropout2, [-1, 8 * 8 * 64])
    
    # dense layer 
    dense1 = dense_layer(pool2_flat, 1024)
    
    # flatten tensor again
    dropout3 = dropout_layer(dense1, mode, 0.4)
    
    # second fully connected layer 
    dense2 = tf.layers.dense(inputs=dropout3, units=512)
    
    # dropout operation
    dropout4 = dropout_layer(dense2, mode, 0.4)
    
    # logits layer
    logits = tf.layers.dense(inputs=dropout4, units=100)
    
    loss = determine_loss(labels, logits, mode)
    train_op = determine_train_op(loss, mode)
    predictions = generate_predictions(logits)
    
    return model_fn_lib.ModelFnOps(
        mode=mode, predictions=predictions, loss=loss, train_op=train_op
    )
    

In [33]:
def generate_accuracy_metric():
    # configure the accuracy metric
    return {
        "accuracy": learn.MetricSpec (
            metric_fn=tf.metrics.accuracy, prediction_key="classes"
        )
    }

def print_evaluate_model(cifar_classifier, data, labels, epoches, subset):
    small_train = np.array_split(data, epoches)[subset]
    small_labels = np.array_split(labels, epoches)[subset]
    evaluate_results = cifar_classifier.evaluate(
        x=small_train, y=small_labels, metrics=generate_accuracy_metric()
    )
    print(evaluate_results)
    return evaluate_results

def serving_input_receiver_fn():
    serialized_tf_example = tf.placeholder(dtype=tf.string, shape=[None], name="input_tensors")
    

def setup_and_train_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/train")
    data = dataset["data"]
    data = data.astype("float32")
    train_data = convert_input_format(data)
    train_labels = convert_output_labels(dataset)
    model_ckpt = "/tmp/cifar100"
    
    # create custom estimator
    cifar_classifier = learn.Estimator (
        model_fn=cnn_model, model_dir="/tmp/cifar100" 
    )
    
    # log predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook (
        tensors=tensors_to_log, every_n_iter=100
    )
    
    # train the model
    with tf.device("/cpu:0"):
        cifar_classifier.fit (
            x=train_data,
            y=train_labels,
            batch_size=64, 
            steps=5240,
            monitors=[logging_hook]
        )
    
#     full_model_dir = cifar_classifier.export_savedmodel(
#         export_dir_base="./models/cifar-100"
#     )
    return cifar_classifier


def test_model(cifar_classifier):
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    # evaluate all test data and print results
    acc = 0
    e_loss = 0
    n_batches = 20
    for i in range (0, n_batches - 1):
        small_eval =  np.array_split(test_data, n_batches)[i]
        small_labs =  np.array_split(test_labels, n_batches)[i]
        eval_results = cifar_classifier.evaluate(
          x=small_eval, y=small_labs, metrics=generate_accuracy_metric())
        print(eval_results)
        acc += eval_results["accuracy"]
        e_loss += eval_results["loss"]

    overall_acc = acc / n_batches
    overall_loss = e_loss/ n_batches
    print("Eval Accuracy = ", overall_acc)
    print("Eval Loss = ", overall_loss) 

In [34]:
classifier = setup_and_train_model()

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_session_config': None, '_keep_checkpoint_max': 5, '_num_worker_replicas': 0, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x13bb60128>, '_master': '', '_tf_random_seed': None, '_keep_checkpoint_every_n_hours': 10000, '_device_fn': None, '_num_ps_replicas': 0, '_save_checkpoints_secs': 600, '_train_distribute': None, '_environment': 'local', '_model_dir': '/tmp/cifar100', '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_task_id': 0, '_evaluation_master': '', '_log_step_count_steps': 100, '_is_chief': True, '_task_type': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None}
train
train
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-28288
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoi

INFO:tensorflow:loss = 1.2506639, step = 28289
INFO:tensorflow:global_step/sec: 1.91785
INFO:tensorflow:probabilities = [[0.00055944 0.00002935 0.0597222  0.00053787 0.00062235 0.0135859
  0.00016271 0.00048349 0.00000482 0.00557645 0.00140624 0.07585341
  0.00335399 0.01263361 0.00033479 0.00004942 0.00462029 0.00001508
  0.00016668 0.00009226 0.00013981 0.00893168 0.0022815  0.00944056
  0.00126586 0.0019498  0.00051931 0.00015619 0.00036676 0.00001265
  0.00011718 0.00068786 0.00054821 0.00007458 0.00004094 0.35296988
  0.00006116 0.00383758 0.00002034 0.00040774 0.07415693 0.00008321
  0.00002402 0.00022112 0.0000198  0.00086406 0.10905442 0.00001223
  0.00016667 0.00003432 0.00126893 0.00066926 0.00000491 0.00011188
  0.0358737  0.0022679  0.00003389 0.00075668 0.00098111 0.00011093
  0.00006553 0.01439605 0.00070393 0.00001378 0.0002497  0.00031118
  0.00013542 0.00046433 0.00001802 0.00403913 0.00081673 0.00436555
  0.00039733 0.05393346 0.0003319  0.00062611 0.00129087 0.000547

INFO:tensorflow:loss = 1.2280409, step = 28389 (51.973 sec)
INFO:tensorflow:global_step/sec: 2.1562
INFO:tensorflow:probabilities = [[0.00011473 0.02503067 0.02467409 0.002578   0.00039739 0.00001616
  0.04894175 0.02975638 0.00172409 0.00066585 0.00003087 0.02618814
  0.00017824 0.00043176 0.02083671 0.0058353  0.00005923 0.00005123
  0.00177786 0.00135988 0.00001686 0.00688652 0.00004059 0.0000195
  0.002744   0.00001651 0.17953858 0.01041309 0.00031475 0.08961122
  0.00031516 0.00048732 0.00093692 0.00011972 0.02372872 0.00017869
  0.00009518 0.00039189 0.01780942 0.00007575 0.0008988  0.00321759
  0.01557344 0.02269443 0.05386198 0.07359203 0.02354769 0.00249674
  0.03628381 0.00015927 0.03516987 0.00654174 0.0001014  0.0015141
  0.00278707 0.00700803 0.00025313 0.01057136 0.00009705 0.00123525
  0.00000981 0.00002525 0.00060069 0.00022199 0.00660656 0.00345323
  0.00512789 0.00258601 0.00026686 0.00014311 0.01502667 0.00006056
  0.00244287 0.00024579 0.00047663 0.00085871 0.000050

INFO:tensorflow:loss = 1.3284142, step = 28489 (46.375 sec)
INFO:tensorflow:global_step/sec: 2.24165
INFO:tensorflow:probabilities = [[0.00000759 0.0000638  0.00056077 0.00000145 0.00000454 0.5487685
  0.         0.00000007 0.0000102  0.00182538 0.00001556 0.00017305
  0.00021219 0.00201266 0.00000068 0.00002592 0.0009364  0.00067344
  0.00000492 0.00002701 0.0006342  0.000015   0.00015209 0.00000396
  0.00000015 0.06612487 0.00000007 0.00000397 0.00007578 0.00000004
  0.00000178 0.00000508 0.00226071 0.00000508 0.00000032 0.00005052
  0.00000761 0.00002699 0.00000015 0.00022767 0.00010391 0.00000158
  0.00004819 0.0000001  0.00000075 0.00000224 0.00022962 0.00000059
  0.0000083  0.0001026  0.00000009 0.00000638 0.00000002 0.00000325
  0.00003448 0.00000333 0.00000001 0.00000669 0.00013325 0.0000003
  0.00000466 0.00000054 0.00000554 0.00000124 0.00000029 0.00000272
  0.00000002 0.00000006 0.00000896 0.00000057 0.00000052 0.00004281
  0.00000095 0.0000065  0.00000002 0.00000001 0.00010

INFO:tensorflow:loss = 1.5752935, step = 28589 (44.635 sec)
INFO:tensorflow:global_step/sec: 2.34802
INFO:tensorflow:probabilities = [[0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.9968086  0.         0.
  0.         0.         0.         0.         0.00000028 0.
  0.00000001 0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.00000001 0.         0.         0.00310196 0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.00008593 0.         0.
  0.         0.         0.         0.         0.0000033  0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0. 

...

INFO:tensorflow:loss = 1.0750667, step = 33089 (64.816 sec)
INFO:tensorflow:global_step/sec: 1.53172
INFO:tensorflow:probabilities = [[0.00000587 0.00000557 0.00000337 0.00220859 0.00000361 0.00000026
  0.00000004 0.00000702 0.00001432 0.00000064 0.00003613 0.00000507
  0.00005686 0.00005296 0.00000153 0.00001409 0.001406   0.00000028
  0.0000003  0.00083911 0.00004101 0.01094292 0.00001369 0.00002745
  0.00001633 0.00001881 0.00011081 0.00000178 0.00001581 0.00000521
  0.0095533  0.00095183 0.00007751 0.00000127 0.00000004 0.00000124
  0.00000003 0.00000543 0.00000811 0.00000772 0.00004968 0.
  0.00000001 0.00000011 0.00010904 0.00000255 0.00015764 0.00000089
  0.00059267 0.00002552 0.00000054 0.00002687 0.00000331 0.00000141
  0.00000018 0.00188822 0.00000025 0.00000172 0.00103006 0.00000526
  0.00000236 0.00000389 0.00006924 0.00000033 0.00000096 0.00000277
  0.00029321 0.0000345  0.00000132 0.00003794 0.00000205 0.00002299
  0.00064888 0.03475752 0.00000105 0.01058619 0.00001984 0.

INFO:tensorflow:loss = 1.086998, step = 33189 (65.918 sec)
INFO:tensorflow:global_step/sec: 1.50315
INFO:tensorflow:probabilities = [[0.         0.         0.         0.00000016 0.00000101 0.
  0.         0.         0.         0.         0.         0.
  0.00000049 0.         0.         0.         0.         0.
  0.00000001 0.         0.         0.00000003 0.         0.00001282
  0.00000002 0.         0.00000003 0.00000017 0.         0.00000001
  0.9784388  0.         0.00000051 0.00000001 0.         0.
  0.         0.         0.00000004 0.00000028 0.00000012 0.
  0.         0.         0.00000003 0.         0.         0.
  0.         0.00009921 0.         0.         0.00000011 0.
  0.         0.00008488 0.00000064 0.         0.00000001 0.
  0.00000012 0.         0.         0.00000007 0.         0.00000001
  0.00000001 0.00000082 0.00000006 0.00001205 0.         0.00039066
  0.00000138 0.00045787 0.00000004 0.00000003 0.00000016 0.
  0.         0.00000001 0.         0.         0.00000001

INFO:tensorflow:loss = 0.82791054, step = 33289 (65.876 sec)
INFO:tensorflow:global_step/sec: 1.47812
INFO:tensorflow:probabilities = [[0.00001003 0.00001901 0.0000003  0.00000003 0.00000001 0.00001186
  0.00000045 0.00000003 0.         0.00000005 0.9948002  0.0000003
  0.         0.00000002 0.00000001 0.         0.00053146 0.
  0.00000185 0.         0.00000282 0.         0.00001302 0.00000003
  0.00001718 0.00238286 0.00000016 0.00000001 0.00015741 0.
  0.0000001  0.         0.0000019  0.         0.00000002 0.0000001
  0.00013819 0.         0.         0.00175995 0.00000083 0.
  0.00000086 0.00000025 0.00001726 0.00000093 0.00000001 0.
  0.         0.00000001 0.0000005  0.00000542 0.         0.0000005
  0.00000042 0.00000092 0.         0.00000001 0.         0.
  0.         0.00008077 0.00000063 0.00000339 0.00000006 0.0000002
  0.00000003 0.00000013 0.         0.         0.00000659 0.00000003
  0.00000008 0.00000003 0.00000176 0.00000002 0.00000001 0.0000003
  0.00000206 0.00000005 0.0

INFO:tensorflow:loss = 1.1504158, step = 33389 (67.643 sec)
INFO:tensorflow:global_step/sec: 1.31312
INFO:tensorflow:probabilities = [[0.00053221 0.002452   0.00281744 0.02870795 0.00874073 0.0118458
  0.00211954 0.00467317 0.00317794 0.00091321 0.03851072 0.00107956
  0.00417538 0.02404889 0.01534393 0.01294251 0.00597546 0.00017148
  0.00097467 0.01657047 0.00085475 0.0066066  0.00085068 0.00021327
  0.00320248 0.01779377 0.01298836 0.08387794 0.00170129 0.00300367
  0.0007455  0.00843725 0.00649898 0.00033568 0.00388169 0.00119007
  0.00078396 0.00320049 0.00230003 0.01583149 0.00134039 0.01298596
  0.00124829 0.0003478  0.01443435 0.01340946 0.01019365 0.00027848
  0.01158657 0.000278   0.0029226  0.00640218 0.00035288 0.00104166
  0.00071272 0.02582438 0.00100908 0.00061466 0.08144015 0.00028911
  0.0006566  0.00467272 0.00030424 0.00127079 0.00170568 0.00924296
  0.01478681 0.00433515 0.00212002 0.0006832  0.00054437 0.00058512
  0.01257779 0.00285821 0.01935752 0.01091199 0.0002

INFO:tensorflow:loss = 1.1516349, step = 33489 (76.175 sec)
INFO:tensorflow:Saving checkpoints for 33513 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:Saving checkpoints for 33528 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:Loss for final step: 1.3397157.


In [35]:
test_model(classifier)

infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:22
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:27
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.424, global_step = 33528, loss = 2.4908679
{'global_step': 33528, 'loss': 2.4908679, 'accuracy': 0.424}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:31
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:36
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.442, global_step = 33528, loss = 2.2866387
{'global_step': 33528, 'loss': 2.2866387, 'accuracy': 0.442}
infer
infer
INFO:t

{'global_step': 33528, 'loss': 2.2949243, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:53
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:28:56
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.448, global_step = 33528, loss = 2.304841
{'global_step': 33528, 'loss': 2.304841, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:58
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:29:01
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.42, global_step = 33528, loss = 2.4275591
{'global_step': 33528